In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import xgboost as xgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint, uniform
from sklearn.externals import joblib

c:\users\kevin song\miniconda3\lib\site-packages\sklearn\externals\joblib\__init__.py:15: DeprecationWarning: sklearn.externals.joblib is deprecated in 0.21 and will be removed in 0.23. Please import this functionality directly from joblib, which can be installed with: pip install joblib. If this warning is raised when loading pickled models, you may need to re-serialize those models with scikit-learn 0.21+.
  warnings.warn(msg, category=DeprecationWarning)


In [2]:
np.random.seed(0)

### Data wrangling

In [3]:
data = pd.read_csv("Master_cleaned.csv.txt", low_memory = False)

In [4]:
data

parcel  location  use  heat  walls  roof  class  condition  \
0       115020720       102    8     8      3     7      2          0   
1       115020730       102    8     8      3     7      2          1   
2       115020740       102    8     1      3     7      2          0   
3       115020750       102    8     1      4     1      2          0   
4       115020770       102    8     6      2     1      2          1   
...           ...       ...  ...   ...    ...   ...    ...        ...   
185163  115020560       102   15     1      7     1      3          1   
185164  115020610       102    8     1      2     1      2          0   
185165  115020640       102   15     1      7     3      3          2   
185166  115020650       102   15     1      2     3      3          1   
185167  115020660       102    8     1      2     1      2          1   

        quality  cool  ...  patio_number  bath_fixture  stories  rooms  \
0             0     1  ...           0.0           3.0      1.0    3.0   
1             0     1  ...           0.0           3.0      1.0    6.0   
2             0     1  ...           1.0           3.0      1.0    5.0   
3             0     1  ...           1.0           3.0      1.0    5.0   
4             0     1  ...           1.0           3.0      1.0    5.0   
...         ...   ...  ...           ...           ...      ...    ...   
185163        1     1  ...           0.0           6.0      1.0    5.0   
185164        0     1  ...           0.0           3.0      1.0    4.0   
185165        1     1  ...           0.0           6.0      1.0    5.0   
185166        1     1  ...           1.0           3.0      1.0    4.0   
185167        1     1  ...           0.0           6.0      1.0    6.0   

        landmeas  fcv_16  fcv_17  fcv_18  fcv_19  fcv_20  
0         3920.0   38000   45956   48305   57189   70102  
1         4760.0   75681   68113   71594   84763  108011  
2            1.0   81320   73188   76929   91078  112637  
3            1.0   97047   87342   91806  108693  130794  
4            1.0   84616   76154   80047   94770  116660  
...          ...     ...     ...     ...     ...     ...  
185163       1.0  122159  122159  126724  144980  162070  
185164       1.0   71496   64346   67635   80076   97082  
185165       1.0   96747   96482   99815  113887  127454  
185166       1.0   92794   92794   96261  110129  124338  
185167       1.0  105133   94620   99456  117749  144151  

[185168 rows x 25 columns]

In [5]:
data.columns

Index(['parcel', 'location', 'use', 'heat', 'walls', 'roof', 'class',
       'condition', 'quality', 'cool', 'landclass', 'age', 'sqft', 'pool_area',
       'garage_capa', 'patio_number', 'bath_fixture', 'stories', 'rooms',
       'landmeas', 'fcv_16', 'fcv_17', 'fcv_18', 'fcv_19', 'fcv_20'],
      dtype='object')

In [6]:
data = data.drop(["parcel"], axis = 1)

In [7]:
data = data.dropna(subset = ["fcv_20"])

In [8]:
y = data[["fcv_20"]]

In [9]:
X = data.drop(["fcv_20"], axis = 1)

In [10]:
model_dmatrix = xgb.DMatrix(data = X, label = y)

### Model training and tuning with randomized cross-validation

In [11]:
xgb_reg = xgb.XGBRegressor(random_state=10, verbosity=3)
param_distrib = {'n_estimators': randint(500, 1000),
                 'max_depth': randint(5, 20),
                 'subsample': uniform(0.5, 0.45),
                 'colsample_bytree': uniform(0.7, 0.3),
                 'learning_rate': uniform(0.001, 0.1),
                 'reg_alpha': uniform(0, 10),
                 'reg_lambda': uniform(0, 10)
}

In [12]:
rs = RandomizedSearchCV(xgb_reg, param_distrib, 10, scoring='neg_mean_squared_error', cv=5)

In [13]:
rs.fit(X, y)
best_params = rs.best_params_
best_rmse = np.sqrt(-rs.best_score_)
print(best_rmse)
xgb_best = rs.best_estimator_

[10:15:14] DEBUG: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\gbm\gbtree.cc:146: Using tree method: 2
[10:15:14] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 72 extra nodes, 0 pruned nodes, max_depth=8
[10:15:14] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 72 extra nodes, 0 pruned nodes, max_depth=8
[10:15:14] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 78 extra nodes, 0 pruned nodes, max_depth=8
[10:15:14] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 72 extra nodes, 0 pruned nodes, max_depth=8
[10:15:14] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 82 extra nodes, 0 pruned nodes, max_depth=8
[10:15:14] INFO: C:\Users\A

[10:15:20] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 308 extra nodes, 0 pruned nodes, max_depth=8
[10:15:20] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 304 extra nodes, 0 pruned nodes, max_depth=8
[10:15:20] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 332 extra nodes, 0 pruned nodes, max_depth=8
[10:15:20] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 308 extra nodes, 0 pruned nodes, max_depth=8
[10:15:20] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 216 extra nodes, 0 pruned nodes, max_depth=8
[10:15:20] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 242 extra nodes, 0 

[10:15:26] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 86 extra nodes, 0 pruned nodes, max_depth=8
[10:15:26] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 140 extra nodes, 0 pruned nodes, max_depth=8
[10:15:26] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 118 extra nodes, 0 pruned nodes, max_depth=8
[10:15:26] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 120 extra nodes, 0 pruned nodes, max_depth=8
[10:15:26] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 130 extra nodes, 0 pruned nodes, max_depth=8
[10:15:27] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 224 extra nodes, 0 p

[10:15:32] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 156 extra nodes, 0 pruned nodes, max_depth=8
[10:15:32] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 126 extra nodes, 0 pruned nodes, max_depth=8
[10:15:32] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 208 extra nodes, 0 pruned nodes, max_depth=8
[10:15:32] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 162 extra nodes, 0 pruned nodes, max_depth=8
[10:15:32] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 170 extra nodes, 0 pruned nodes, max_depth=8
[10:15:32] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 134 extra nodes, 0 

[10:15:37] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 266 extra nodes, 0 pruned nodes, max_depth=8
[10:15:37] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 138 extra nodes, 0 pruned nodes, max_depth=8
[10:15:37] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 332 extra nodes, 0 pruned nodes, max_depth=8
[10:15:37] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 152 extra nodes, 0 pruned nodes, max_depth=8
[10:15:38] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 144 extra nodes, 0 pruned nodes, max_depth=8
[10:15:38] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 106 extra nodes, 0 

...

[11:50:39] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1898 extra nodes, 0 pruned nodes, max_depth=11
[11:50:39] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1190 extra nodes, 0 pruned nodes, max_depth=11
[11:50:39] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 854 extra nodes, 0 pruned nodes, max_depth=11
[11:50:39] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 786 extra nodes, 0 pruned nodes, max_depth=11
[11:50:39] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 958 extra nodes, 0 pruned nodes, max_depth=11
[11:50:39] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1516 extra n

[11:50:47] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 860 extra nodes, 0 pruned nodes, max_depth=11
[11:50:47] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1062 extra nodes, 0 pruned nodes, max_depth=11
[11:50:47] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 720 extra nodes, 0 pruned nodes, max_depth=11
[11:50:48] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1080 extra nodes, 0 pruned nodes, max_depth=11
[11:50:48] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1146 extra nodes, 0 pruned nodes, max_depth=11
[11:50:48] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1558 extra 

[11:51:04] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1502 extra nodes, 0 pruned nodes, max_depth=11
[11:51:04] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 2046 extra nodes, 0 pruned nodes, max_depth=11
[11:51:04] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1060 extra nodes, 0 pruned nodes, max_depth=11
[11:51:04] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1088 extra nodes, 0 pruned nodes, max_depth=11
[11:51:04] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 994 extra nodes, 0 pruned nodes, max_depth=11
[11:51:04] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1120 extra

[11:51:12] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1652 extra nodes, 0 pruned nodes, max_depth=11
[11:51:12] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1844 extra nodes, 0 pruned nodes, max_depth=11
[11:51:13] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 922 extra nodes, 0 pruned nodes, max_depth=11
[11:51:13] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1026 extra nodes, 0 pruned nodes, max_depth=11
[11:51:13] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1986 extra nodes, 0 pruned nodes, max_depth=11
[11:51:13] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 782 extra 

[11:51:21] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 772 extra nodes, 0 pruned nodes, max_depth=11
[11:51:21] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1522 extra nodes, 0 pruned nodes, max_depth=11
[11:51:21] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1006 extra nodes, 0 pruned nodes, max_depth=11
[11:51:21] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 770 extra nodes, 0 pruned nodes, max_depth=11
[11:51:22] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 780 extra nodes, 0 pruned nodes, max_depth=11
[11:51:22] INFO: C:\Users\Administrator\workspace\xgboost-win64_release_1.0.0\src\tree\updater_prune.cc:89: tree pruning end, 1110 extra n

### Prediction

In [14]:
y_hat_best = xgb_best.predict(X)
np.sqrt(mean_squared_error(y, y_hat_best))

2028.08815045954

In [20]:
from sklearn.externals import joblib

joblib.dump(xgb_best, 'xgb_best.pkl')

['xgb_best.pkl']

In [21]:
print(best_params)

{'colsample_bytree': 0.7297841051076921, 'learning_rate': 0.09798090677467489, 'max_depth': 11, 'n_estimators': 619, 'reg_alpha': 1.7090958513604515, 'reg_lambda': 3.58152166969525, 'subsample': 0.8378087635483054}


### Adapting model to forecast year 21 fcvs

In [2]:
data = pd.read_csv("Master_cleaned.csv.txt", low_memory = False)

In [3]:
data = data.drop(["parcel"], axis = 1)

In [4]:
data

location  use  heat  walls  roof  class  condition  quality  cool  \
0            102    8     8      3     7      2          0        0     1   
1            102    8     8      3     7      2          1        0     1   
2            102    8     1      3     7      2          0        0     1   
3            102    8     1      4     1      2          0        0     1   
4            102    8     6      2     1      2          1        0     1   
...          ...  ...   ...    ...   ...    ...        ...      ...   ...   
185163       102   15     1      7     1      3          1        1     1   
185164       102    8     1      2     1      2          0        0     1   
185165       102   15     1      7     3      3          2        1     1   
185166       102   15     1      2     3      3          1        1     1   
185167       102    8     1      2     1      2          1        1     1   

        landclass  ...  patio_number  bath_fixture  stories  rooms  landmeas  \
0               0  ...           0.0           3.0      1.0    3.0    3920.0   
1               0  ...           0.0           3.0      1.0    6.0    4760.0   
2               1  ...           1.0           3.0      1.0    5.0       1.0   
3               1  ...           1.0           3.0      1.0    5.0       1.0   
4               0  ...           1.0           3.0      1.0    5.0       1.0   
...           ...  ...           ...           ...      ...    ...       ...   
185163          0  ...           0.0           6.0      1.0    5.0       1.0   
185164          1  ...           0.0           3.0      1.0    4.0       1.0   
185165          0  ...           0.0           6.0      1.0    5.0       1.0   
185166          0  ...           1.0           3.0      1.0    4.0       1.0   
185167          0  ...           0.0           6.0      1.0    6.0       1.0   

        fcv_16  fcv_17  fcv_18  fcv_19  fcv_20  
0        38000   45956   48305   57189   70102  
1        75681   68113   71594   84763  108011  
2        81320   73188   76929   91078  112637  
3        97047   87342   91806  108693  130794  
4        84616   76154   80047   94770  116660  
...        ...     ...     ...     ...     ...  
185163  122159  122159  126724  144980  162070  
185164   71496   64346   67635   80076   97082  
185165   96747   96482   99815  113887  127454  
185166   92794   92794   96261  110129  124338  
185167  105133   94620   99456  117749  144151  

[185168 rows x 24 columns]

In [5]:
fcv_19 = pd.DataFrame(data["fcv_20"].tolist())

In [6]:
fcv_19.columns = ["fcv_19"]

In [7]:
X = data.drop(["fcv_19", "fcv_20"], axis = 1)

In [8]:
X = pd.concat([X, fcv_19], axis = 1)

In [9]:
X

location  use  heat  walls  roof  class  condition  quality  cool  \
0            102    8     8      3     7      2          0        0     1   
1            102    8     8      3     7      2          1        0     1   
2            102    8     1      3     7      2          0        0     1   
3            102    8     1      4     1      2          0        0     1   
4            102    8     6      2     1      2          1        0     1   
...          ...  ...   ...    ...   ...    ...        ...      ...   ...   
185163       102   15     1      7     1      3          1        1     1   
185164       102    8     1      2     1      2          0        0     1   
185165       102   15     1      7     3      3          2        1     1   
185166       102   15     1      2     3      3          1        1     1   
185167       102    8     1      2     1      2          1        1     1   

        landclass  ...  garage_capa  patio_number  bath_fixture  stories  \
0               0  ...          0.0           0.0           3.0      1.0   
1               0  ...          0.0           0.0           3.0      1.0   
2               1  ...          0.0           1.0           3.0      1.0   
3               1  ...          0.0           1.0           3.0      1.0   
4               0  ...          1.0           1.0           3.0      1.0   
...           ...  ...          ...           ...           ...      ...   
185163          0  ...          1.0           0.0           6.0      1.0   
185164          1  ...          0.0           0.0           3.0      1.0   
185165          0  ...          1.0           0.0           6.0      1.0   
185166          0  ...          1.0           1.0           3.0      1.0   
185167          0  ...          1.0           0.0           6.0      1.0   

        rooms  landmeas  fcv_16  fcv_17  fcv_18  fcv_19  
0         3.0    3920.0   38000   45956   48305   70102  
1         6.0    4760.0   75681   68113   71594  108011  
2         5.0       1.0   81320   73188   76929  112637  
3         5.0       1.0   97047   87342   91806  130794  
4         5.0       1.0   84616   76154   80047  116660  
...       ...       ...     ...     ...     ...     ...  
185163    5.0       1.0  122159  122159  126724  162070  
185164    4.0       1.0   71496   64346   67635   97082  
185165    5.0       1.0   96747   96482   99815  127454  
185166    4.0       1.0   92794   92794   96261  124338  
185167    6.0       1.0  105133   94620   99456  144151  

[185168 rows x 23 columns]

In [10]:
model = joblib.load("xgb_best.pkl")

In [11]:
predictions = model.predict(X)

In [12]:
print(predictions)

[ 80289.734 121501.38  125526.24  ... 132673.14  132299.61  157582.23 ]
